## Feature Engineering - Final - Step 3

### Imports

In [ ]:
!pip install thefuzz
!pip install rapidfuzz

     |████████████████████████████████| 3.4 MB 27.8 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-f19d2a8a-df82-4a76-80af-00c8c19f0c46/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-f19d2a8a-df82-4a76-80af-00c8c19f0c46/bin/python -m pip install --upgrade pip' command.


In [ ]:
import pandas as pd
import glob
import rapidfuzz.utils
import thefuzz
from thefuzz import process, utils
from copy import copy
import ast
from rapidfuzz import fuzz as rapidfuzz

from pyspark.sql.types import *
from pyspark.sql import functions as F

VALUE_ERROR = -1

# this boolean marks code related to profiles dataset
pr = True

### Loading chosen positions and data

In [ ]:
choices_new = spark.read.parquet("dbfs:/user_data/g37/choices_new.parquet")
choices = list(choices_new.toPandas().to_dict()['0'].values())

In [ ]:
if pr:
    dir_path = "dbfs:/user_data/g37/"
    file_name = "profiles_new.parquet"
    file_path = dir_path + file_name
    profiles_new = spark.read.parquet(file_path, header = True)
dir_path = "dbfs:/user_data/g37/"
file_name = "skills_and_degrees_true_narroweddd.parquet"
file_path = dir_path + file_name
skills_new = spark.read.parquet(file_path, header = True)

### convert to chosen positions for profiles

In [ ]:
def get_match(title):
    matches = process.extractOne(title, choices, scorer=rapidfuzz.token_set_ratio,
                                 processor=thefuzz.process.default_processor)
    if matches[1] < 90:
        return None
    return matches[0]
get_match_udf = F.udf(get_match)

In [ ]:
dfsk = skills_new.select("*")
if pr:
    df = profiles_new.select("*")
    df = df.withColumn('narrow_position', get_match_udf(F.col('position')))
    df = df.dropna(subset=['narrow_position'])
    df = df.withColumnRenamed("dp_list", "degree_cleaned")

### Convert Experience to Relevant Experience

In [ ]:
map_df = spark.sql("SELECT * FROM hive_metastore.default.alternative_titles_map").to_pandas_on_spark().drop_duplicates(subset=['alternative_titles'],keep='first')
alt_df = spark.sql("SELECT * FROM hive_metastore.default.alternate_titles").to_pandas_on_spark().rename({'Alternate Title':'alternative_titles','Title':'title'}, axis=1)
map_dict = map_df.to_dict()
alt_dict = alt_df.to_dict()
def convert_alt(alt,gen):
    if alt[:len(gen)] != gen:
        return alt
    else:
        return alt.split("-")[-1].strip()
alt_to_gen = {convert_alt(alt,gen): gen for alt, gen in zip(map_dict['alternative_titles'].values(), map_dict['title'].values())}
gen_to_alts = {gen: eval(alt_list) for gen, alt_list in zip(alt_dict['title'].values(), alt_dict['alternative_titles'].values())}

narrowed_size = len(choices)
minimum_match_score = 90

def find_narrowed_match(pos_title, exp_title):
    title_item = str(alt_to_gen[pos_title])
    find_match_in = gen_to_alts[title_item]
    matches = process.extractOne(exp_title, find_match_in, scorer=rapidfuzz.token_set_ratio, processor=thefuzz.process.default_processor)
    return matches[0]

/databricks/spark/python/pyspark/sql/dataframe.py:3612: FutureWarning: DataFrame.to_pandas_on_spark is deprecated. Use DataFrame.pandas_api instead.
  warnings.warn(
/databricks/spark/python/pyspark/sql/dataframe.py:3612: FutureWarning: DataFrame.to_pandas_on_spark is deprecated. Use DataFrame.pandas_api instead.
  warnings.warn(


In [ ]:
if pr:
    def convert_experience(item):
        item = eval(item)
        orig_pos = item['position']
        pos = item['narrow_position']
        exp_titles = item['title']
        duration_short = item['duration_in_years']
        proccessed_exp_titles = []
        proccessed_exp_duration = []
        years_relevant_experience = 0
        years_in_position = 0
        proccessed_exp_titles_rapidfuzz = []
        proccessed_exp_duration_rapidfuzz = []
        years_relevant_experience_rapidfuzz = 0
        years_in_position_rapidfuzz = 0
        for i, exp in enumerate(exp_titles):
            rapidfuzz_res = rapidfuzz.partial_token_set_ratio(orig_pos, exp) >= minimum_match_score
            match_exp_title = find_narrowed_match(pos, exp_titles[i])
            if rapidfuzz_res:
                years_in_position_rapidfuzz += duration_short[i]
            else:
                if match_exp_title != VALUE_ERROR:
                    years_relevant_experience_rapidfuzz += duration_short[i]
                    proccessed_exp_titles_rapidfuzz.append(str(match_exp_title))
                    proccessed_exp_duration_rapidfuzz.append(float(duration_short[i]))
            if match_exp_title != VALUE_ERROR:
                if match_exp_title == pos:
                    years_in_position += duration_short[i]
                else:
                    years_relevant_experience += duration_short[i]
                    proccessed_exp_titles.append(str(match_exp_title))
                    proccessed_exp_duration.append(float(duration_short[i]))
        return {"years_relevant_experience": float(years_relevant_experience), "years_in_position": float(years_in_position), "processed_exp_titles": proccessed_exp_titles, "processed_exp_duration": proccessed_exp_duration, "years_relevant_experience_rapidfuzz": float(years_relevant_experience_rapidfuzz), "years_in_position_rapidfuzz": float(years_in_position_rapidfuzz), "processed_exp_titles_rapidfuzz": proccessed_exp_titles_rapidfuzz, "processed_exp_duration_rapidfuzz": proccessed_exp_duration_rapidfuzz}

        fun_udf = F.udf(convert_experience, returnType=StructType()\
            .add("years_relevant_experience", FloatType(), False) \
                .add("years_in_position", FloatType(), False) \
                        .add("processed_exp_titles", ArrayType(StringType()), False) \
                            .add("processed_exp_duration", ArrayType(FloatType()), False) \
                                .add("years_relevant_experience_rapidfuzz", FloatType(), False) \
                                    .add("years_in_position_rapidfuzz", FloatType(), False) \
                                            .add("processed_exp_titles_rapidfuzz", ArrayType(StringType()), False) \
                                                .add("processed_exp_duration_rapidfuzz", ArrayType(FloatType()), False))

In [ ]:
def convert_experience_skills(item):
    try:
        item = eval(item)
        item['experience_titles']
        item['experience_durations']
        item['narrow_position']
        item['position']
    except:
        try:
            item = eval(item.replace("null",'\"null\"'))
            # print(item)
            for k in item.keys():
                v_parsed = []
                for v in item[k]:
                    if v != "null":
                        v_parsed.append(v)
                item[k] = v_parsed
            item['experience_titles']
            item['experience_durations']
            item['narrow_position']
            item['position']
        except:
            return None
    orig_pos = item['position']
    pos = item['narrow_position']
    exp_titles = item['experience_titles']
    duration_short = item['experience_durations']
    proccessed_exp_titles = []
    proccessed_exp_duration = []
    years_relevant_experience = 0
    for i, exp in enumerate(exp_titles):
        match_exp_title = find_narrowed_match(pos, exp_titles[i])
        if match_exp_title != VALUE_ERROR:
            years_relevant_experience += duration_short[i]
            proccessed_exp_titles.append(str(match_exp_title))
            proccessed_exp_duration.append(float(duration_short[i]))
        else:
            years_relevant_experience += duration_short[i]
            proccessed_exp_titles.append(exp_titles[i])
            proccessed_exp_duration.append(float(duration_short[i]))
    return {"years_relevant_experience": float(years_relevant_experience), "processed_exp_titles": proccessed_exp_titles, "processed_exp_duration": proccessed_exp_duration}

funsk_udf = F.udf(convert_experience_skills, returnType=StructType()\
    .add("years_relevant_experience", FloatType(), False) \
            .add("processed_exp_titles", ArrayType(StringType()), False) \
                .add("processed_exp_duration", ArrayType(FloatType()), False))

In [ ]:
dfsk_input = dfsk.withColumn("input_col", F.to_json(F.struct([F.col(x) for x in dfsk.columns]))).dropna(subset="input_col")
dfsk_scount = dfsk_input.select("*")
if pr:
    df_input = df.withColumn("input_col", F.to_json(F.struct([F.col(x) for x in df.columns])))
    df_scount = df_input.select("*")

In [ ]:
if pr:
    df_scount_res = df_scount.withColumn("res_col", fun_udf(F.col("input_col"))).dropna(subset="res_col")
dfsk_scount_res = dfsk_scount.withColumn("res_col", funsk_udf(F.col("input_col"))).dropna(subset="res_col")

Out[24]: 16365

### restructuring result and saving

In [ ]:
if pr:
    df_expanded = df_scount_res.select("*", "res_col.years_relevant_experience", "res_col.years_in_position", "res_col.processed_exp_titles", "res_col.processed_exp_duration")
dfsk_expanded = dfsk_scount_res.select("*", "res_col.years_relevant_experience", "res_col.processed_exp_titles", "res_col.processed_exp_duration")

In [ ]:
if pr:
    df_expanded.write.parquet("dbfs:/user_data/g37/profiles_final.parquet")
dfsk_expanded.write.parquet("dbfs:/user_data/g37/skills_final___sfn.parquet")

In [ ]:
if pr:
    dir_path = "dbfs:/user_data/g37/"
    file_name = "profiles_final.parquet"
    file_path = dir_path + file_name
    profiles_final = spark.read.parquet(file_path, header = True)
skills_final_sfn = spark.read.parquet("dbfs:/user_data/g37/skills_final___sfn.parquet")

In [ ]:
skills_final_cleaned_sfn = skills_final_sfn.select(
    "id",
    "skills",
    F.col("position").alias("position_original"),
    F.col("job_summary").alias("job_summary_original"),
    F.col("education_degree_gen").alias("education_degrees_original"), 
    F.col("education_field").alias("education_fields_original"),
    F.col("experience_titles").alias("experience_titles_original"),
    F.col("experience_durations").alias("experience_durations_original"),
    F.col("narrow_position").alias("position"),
    F.col("education_degree").alias("education_degrees"),
    F.col("processed_exp_titles").alias("experience_titles"),
    F.col("processed_exp_duration").alias("experience_durations"),
    F.col("years_relevant_experience").alias("total_years_relevant_experience"),
    )

skills_final_cleaned_sfn.display()

id skills position_original job_summary_original education_degrees_original education_fields_original experience_titles_original experience_durations_original position education_degrees experience_titles experience_durations total_years_relevant_experience 103079215104 List(Customer service, Communication, Cash handling, Store preparation, Cleaning, Safety, Medical insurance, Dental insurance, Vision insurance, Life insurance, HSA, Flexible spending, Transit benefits, 401k, Paid vacation, Flexible schedules, Training, Sick leave, Referral bonus, Career growth) Retail Assistant Manager- NJ Assistant Store Manager
This position qualifies for Daily Pay!!
Location: Montague, NJ
Apply Online: bit.ly/AMGcareers
Atlantis Fresh Market is a leading Convenience Store brand in the Northeast, and we are GROWING! If you thrive in a fast-paced, customer-facing role, and are looking for a new opportunity to GROW your career, Apply Online today to begin your journey with a winning Team that strives to achieve Customer Service Excellence every day!
Job Snapshot
As an Assistant Manager you will handle management level tasks when the manager is absent, including motivating your valued team in providing excellent customer service by greeting and communicating with customers, working the register, preparing the store, and maintaining a clean, safe environment. A detailed list of duties, responsibilities, and physical requirements is provided in the official Job Description for this role.
Full Time Employees Appreciate
Medical, Dental, Vision Insurance
Company Paid and Voluntary Life Insurance
HSA, Flexible Spending, Transit Benefits
401k with Company Match
Paid Vacation Time
All Employees Are Offered
Flexible Schedules
Paid Training
Paid Sick Leave
Referral Bonus
Opportunity for Career Growth
Show more
Show less List() List() List() List() Retail Manager List() List() List() 0.0 103079215105 List(Customer service, Property maintenance, Sales, PointofSale (POS) system, Light cleaning, Landscaping, Basic computer skills, Driver's license, Reliable transportation, Ability to stand sit kneel crouch crawl bend climb or balance on a ladder) Assistant Property Manager Overview
At CubeSmart, our culture makes the difference. When we say it’s what’s
inside
that counts, we are saying “you count”
Responsibilities
What CubeSmart Self-Storage offers:
Excellent Schedule – Most shifts end at 6:00 p.m. and Sundays off*
Competitive Hourly Pay & Bonus
Paid Time Off – Vacation, Sick, & Holidays
Generous Health Benefits
401k Retirement Plan with Company Match
Tuition Reimbursement
Self-Storage Discounts
In your role at CubeSmart Self-Storage, you will be required to manage and maintain your property. This includes skills in both customer service and property maintenance.
The Assistant Property Manager is responsible for….
Customer Service
Developing customer relationships by identifying self-storage needs and providing appropriate solutions while delivering a WOW! or 5-Star service.
Interacting face to face with customers, providing excellent service, and building rapport.
Meeting monthly sales goals and metrics.
Walking the property to perform lock checks and showing units to customers.
Working both independently and on a team renting self-storage spaces, selling store merchandise, managing the leasing process, accepting payments utilizing our Point-of-Sale System (POS), completing daily bank deposits, and making courtesy calls to customers regarding late payments.
Property Maintenance
Physical requirements include daily walks of the property, cleaning the units and the property, opening, and closing of the storage doors (up to 50 lbs.)
Maintaining facility which includes mopping, sweeping, changing light bulbs, cleaning out storage units, and similar light activities.
Keeping a clean and safe storage facility to ensure condition meets company guidelines (i.e., clean restrooms, landscaping, parking, and paving, fence, walls, doors)
You’ll love working here because…


In [ ]:
skills_final_cleaned_sfn.write.parquet("dbfs:/user_data/g37/skills_final_cleaned___sfn.parquet")
skills_final_cleaned_sfa = spark.read.parquet("dbfs:/user_data/g37/skills_final_cleaned_sfa.parquet")
skills_final_cleaned_sfn.groupBy("position").count().display()
skills_final_cleaned_sfa.groupBy("position").count().display()

position count Finance Manager 51 National Account Manager 54 Project Management Manager 72 Financial Manager 21 Job Service Specialist 9 President 27 Building Manager 15 Planning Analyst 24 Health Manager 93 Analyst Programmer 19 Athletic Trainer 43 Bookkeeper 25 Nurse Manager 261 HR Generalist (Human Resources Generalist) 55 City Engineer 3 Support Analyst 20 Billing Specialist 10 Assistant Professor 145 Customer Engineer 6 Basketball Coach 5 Occupational Therapist (OT) 84 Industrial Manager 22 Gas Operations Manager 321 Aerospace Engineer 5 Development Specialist 44 Builder 19 Health Educator 13 Procurement Manager 32 Civil Engineer 130 Logistics Analyst 8 Receptionist 67 Account Executive 405 Nursing Assistant 22 Director 354 Project Leader 7 C++ Professor 47 Lawyer 32 Environmental Engineer 12 Relationship Manager 22 Learning Manager 15 Registered Nurse Clinical Information Systems Coordinator (RN Clinical Information Systems Coordinator) 6 .NET Developer 31 Physician's Assistant 219 Clinical Coordinator 59 Human Resources Manager (HR Manager) 49 Delivery Manager 17 Python Developer 7 School Nurse 32 Controls Engineer 62 Graphic Designer 29 Group Manager 20 Executive Assistant 168 Integration Engineer 15 Application Customer Service Representative 169 Certified Executive Chef (CEC) 34 University Professor 2 Emergency Department RN (Emergency Department Registered Nurse) 320 Education Teacher 17 Clinical Psychologist 65 Hospital Supervisor 8 Health Specialist 62 Dental Assistant (DA) 10 Administrative Manager 10 Program Assistant 15 Electrician 53 Restaurant Manager 332 Medical Manager 12 Staff Engineer 48 Counsel 70 Die Maintenance Technician 128 Event Manager 18 Chemical Engineer 8 Customer Service Representative 172 Statistician 5 Advisor 675 Chemist 55 Office Manager 171 Elementary Teacher 4 Market Manager 30 Health Coach 17 Sales Account Manager 70 Logistics Manager 19 Compliance Manager 44 Software Manager 23 Electronics Engineer 20 Certified Technician 11 Embedded Engineer 6 Foreman 88 Financial Planner 23 Industrial Engineer 12 Licensed Therapist 89 Clinic Assistant 11 Technical Manager 85 Machine Learning Engineer 14 Technical Engineer 28 Marketing Executive 13 Legal Assistant 18 Technical Writer 51 Quality Assurance Specialist 14 Hospital Manager 15 Recruiter 83 Full Stack Web Developer 13 Systems Specialist 14 Claims Adjuster 15 Corporate Manager 42 High School Coach 8 Sales Leader 59 Training Manager 90 Web Development Manager 120 Chef Manager 24 Research Fellow 18 Practice Manager 27 Language Pathologist 13 School Counselor 47 Pharmacy Manager 39 Research Scientist 31 Sourcing Manager 10 Business Analyst 202 Software Architect 9 Marketing Associate 7 Healthcare Manager 25 Physicist 16 Academic Advisor 1 Interior Designer 14 Division Manager 16 Supply Chain Analyst 11 DevOps Engineer 37 Data Scientist 50 Property Manager 118 Manufacturing Engineer 75 Credit Manager 9 General Contractor 6 Hospitalist 159 Purchasing Manager 23 Intelligence 73 Sales Manager 217 General Manager (GM) 151 Bar Manager 10 Area Manager 96 Marketing Analyst 9 Warehouse Associate 32 Warehouse Manager 60 Business Executive 35 Software Developer 30 Medical Supervisor 15 Regional Manager 54 Pediatric Nurse 42 Licensed Counselor 112 HR Business Partner (Human Resources Business Partner) 41 Mechanical Engineer 171 Claims Specialist 16 Electrical Engineer 210 Paralegal 50 Technologist 1448 Data Manager 84 Chiropractor 5 C Developer 216 Tax Manager 70 Software Quality Engineer 34 Customer Specialist 23 Nurse Practitioner (NP) 308 Environmental Scientist 25 Business Data Analyst 14 Retail Manager 143 Family Practitioner 65 Accountant 475 Project Assistant 45 Java Developer 28 Customer Manager 119 Administrator 314 Attorney 370 Clinical Supervisor 86 Construction Superintendent 145 Facilities Project Manager 22 Construction Manager 224 Executive Chef (Ex Chef) 24 Maker 5 Support Manager 21 Architect Manager 8 Real Estate Manager 21 Web Operations 

position count National Account Manager 31 Finance Manager 12 Project Management Manager 25 Job Service Specialist 3 Financial Manager 4 President 6 Analyst Programmer 7 Health Manager 26 Athletic Trainer 9 Bookkeeper 11 Nurse Manager 78 HR Generalist (Human Resources Generalist) 18 Support Analyst 7 Billing Specialist 4 Assistant Professor 27 Customer Engineer 2 Occupational Therapist (OT) 22 Industrial Manager 5 Gas Operations Manager 78 Builder 5 Development Specialist 8 Civil Engineer 39 Procurement Manager 12 Logistics Analyst 4 Receptionist 33 Account Executive 189 Nursing Assistant 14 Director 129 Project Leader 6 C++ Professor 5 Lawyer 18 Relationship Manager 7 Learning Manager 7 Registered Nurse Clinical Information Systems Coordinator (RN Clinical Information Systems Coordinator) 2 .NET Developer 11 Physician's Assistant 65 Clinical Coordinator 29 Human Resources Manager (HR Manager) 19 Delivery Manager 6 School Nurse 16 Controls Engineer 22 Graphic Designer 13 Group Manager 5 Executive Assistant 73 Integration Engineer 3 Application Customer Service Representative 50 Certified Executive Chef (CEC) 15 University Professor 1 Emergency Department RN (Emergency Department Registered Nurse) 91 Education Teacher 6 Clinical Psychologist 13 Health Specialist 10 Hospital Supervisor 3 Program Assistant 5 Administrative Manager 3 Electrician 22 Restaurant Manager 111 Medical Manager 4 Counsel 15 Staff Engineer 15 Die Maintenance Technician 45 Event Manager 3 Customer Service Representative 57 Advisor 192 Chemist 21 Office Manager 61 Market Manager 10 Elementary Teacher 3 Health Coach 5 Sales Account Manager 26 Logistics Manager 7 Electronics Engineer 11 Compliance Manager 7 Software Manager 10 Foreman 28 Financial Planner 9 Industrial Engineer 9 Licensed Therapist 31 Technical Manager 19 Clinic Assistant 4 Machine Learning Engineer 2 Technical Engineer 9 Marketing Executive 9 Technical Writer 9 Quality Assurance Specialist 3 Recruiter 19 Full Stack Web Developer 7 Systems Specialist 8 Claims Adjuster 5 Corporate Manager 7 High School Coach 1 Web Development Manager 42 Sales Leader 20 Training Manager 28 Chef Manager 8 Research Fellow 9 Practice Manager 12 School Counselor 21 Language Pathologist 6 Research Scientist 13 Pharmacy Manager 12 Business Analyst 72 Healthcare Manager 10 Physicist 5 Interior Designer 6 Division Manager 3 Supply Chain Analyst 1 DevOps Engineer 11 Data Scientist 10 Property Manager 33 Manufacturing Engineer 30 Credit Manager 3 Hospitalist 44 Purchasing Manager 3 Intelligence 23 Sales Manager 58 General Manager (GM) 55 Bar Manager 4 Area Manager 36 Marketing Analyst 4 Warehouse Manager 15 Warehouse Associate 14 Business Executive 15 Software Developer 15 Pediatric Nurse 11 Regional Manager 15 Mechanical Engineer 67 Licensed Counselor 28 Claims Specialist 2 HR Business Partner (Human Resources Business Partner) 6 Electrical Engineer 83 Paralegal 14 Technologist 391 Data Manager 22 Chiropractor 2 C Developer 73 Software Quality Engineer 18 Tax Manager 21 Customer Specialist 6 Nurse Practitioner (NP) 84 Environmental Scientist 8 Business Data Analyst 10 Retail Manager 44 Family Practitioner 17 Accountant 137 Project Assistant 8 Java Developer 10 Customer Manager 47 Attorney 109 Administrator 105 Clinical Supervisor 26 Construction Superintendent 42 Construction Manager 71 Executive Chef (Ex Chef) 9 Maker 4 Support Manager 9 Real Estate Manager 4 Web Operations Specialist 3 Media Manager 8 Registered Health Nurse 66 Audit Associate 2 Supply Chain Manager 6 System Analyst 9 Field Service Technician (Field Service Tech) 24 Services Manager 58 Development Engineer 11 Department Manager 45 Economist 3 Data Consultant 2 Health Assistant 10 Project Manager (PM) 89 Data Architect 11 Transportation Manager 4 Mechanical Design Engineer 4 Geologist 2 Environmental Manager 3 Software Engineer 122 City Manager 3 Medical RN (Medical Registered Nurse) 19 Sales Development Representative 7 Dentist 101 Systems Engineering M

In [ ]:
skills_neat = skills_final_cleaned_sfn.select(skills_final_cleaned_sfa.columns).union(skills_final_cleaned_sfa)
skills_neat.write.parquet("dbfs:/FileStore/g37/skills_final_cleaned____master.parquet")

Out[48]: 21482

In [ ]:
profiles_final_cleaned = profiles_final.select(
    "id",
    F.col("position").alias("position_original"),
    F.col("education.degree").alias("education_degrees_original"), 
    F.col("education.field").alias("education_fields_original"),
    F.col("title").alias("experience_titles_original"),
    F.col("duration_in_years").alias("experience_durations_original"),
    F.col("narrow_position").alias("position"),
    F.col("degree_cleaned").alias("education_degrees"),
    F.col("processed_exp_titles").alias("experience_titles"),
    F.col("processed_exp_duration").alias("experience_durations"),
    F.col("years_in_position").alias("total_years_in_position"),
    F.col("years_relevant_experience").alias("total_years_relevant_experience"),
    F.col("res_col.processed_exp_titles_rapidfuzz").alias("_rapidfuzz_experience_titles"),
    F.col("res_col.processed_exp_duration_rapidfuzz").alias("_rapidfuzz_experience_durations"),
    F.col("res_col.years_in_position_rapidfuzz").alias("_rapidfuzz_total_years_in_position"),
    F.col("res_col.years_relevant_experience_rapidfuzz").alias("_rapidfuzz_total_years_relevant_experience"))
    

#### fixing education degree "AS" recognized from string containing the word "as"

In [ ]:
from pyspark.sql.functions import col, array_except, when, array_contains

# Checking if "AS" is present in education_degrees_original array
contains_as_condition = ~array_contains(col("education_degrees_original"), "AS")

# If "AS" is present in education_degrees and not present in education_degrees_original, remove it
updated_df = profiles_final_cleaned.withColumn(
    "education_degrees",
    when(
        contains_as_condition,
        array_except(col("education_degrees"), F.array(F.lit("AS")))
    ).otherwise(col("education_degrees"))
)

In [ ]:
updated_df.write.parquet("dbfs:/user_data/g37/profiles_final_cleaned.parquet")